In [23]:
import lzma
import csv
import re

def readInput(dir):
    X = []
    if 'xz' in dir:
        with lzma.open(dir) as f:
            for line in f:
                text = line.decode('utf-8')
                text = text.split('\t')
                X.append(text)
    else:
        with open(dir, encoding='utf8', errors='ignore') as f:
            for line in f:
                X. append(line.replace('\n',''))
    return X

def writeOutput(output, dir):
    with open(dir, 'w', newline='') as f:
        writer = csv.writer(f)
        for row in output:
            writer.writerow([row])

In [2]:
X = readInput('train/train.tsv.xz')

In [3]:
len(X[:10000])

10000

In [4]:
import pandas as pd

Xcut = X[:10000]


train = pd.DataFrame(Xcut, columns=['Beginning', 'End', 'Title', 'Source', 'X'])
train['Y'] = train.apply(lambda x: (float(x.Beginning) + float(x.End))/2, axis=1)
train = train.drop(columns=['Beginning', 'End', 'Title', 'Source'])

In [5]:
from sklearn import linear_model
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline

estimators = [('tfidf', TfidfVectorizer()), ('linearRegression', linear_model.LinearRegression())]
model = Pipeline(estimators)

In [6]:
model.fit(train.X, train.Y)

Pipeline(steps=[('tfidf', TfidfVectorizer()),
                ('linearRegression', LinearRegression())])

In [7]:
dev0X = readInput('dev-0/in.tsv')
dev0Expected = readInput('dev-0/expected.tsv')
dev0Predicted = model.predict(dev0X)

In [10]:
dev0Predicted.tolist()

[1840.1873506530203,
 1955.5054038330952,
 1957.188169072484,
 1982.9915478948235,
 1922.1391249931735,
 1953.8540804466156,
 1994.2253928270109,
 1928.8733549680846,
 1878.2307361714463,
 1932.1935071045214,
 1874.0086844537832,
 1990.5539090713487,
 1891.3963033388222,
 1916.1311071475943,
 1965.8835164477582,
 1944.1484754660025,
 1981.2925041285077,
 1969.2231979814874,
 1833.8734424736388,
 1962.692041027358,
 1881.8458215986618,
 1867.336166647721,
 1923.579708076516,
 1918.2099905900664,
 1896.2953230746057,
 1953.899814150262,
 1912.3026680112946,
 1933.100765112436,
 1987.5536174030713,
 1953.1828450164787,
 1907.4139724517734,
 1907.4602781805127,
 1876.2301111417316,
 1894.5329130511432,
 1898.901328501861,
 1909.3986406773226,
 1889.9044917531517,
 1876.3801241447957,
 2009.4570741782811,
 1953.2668326737992,
 1855.4125267298964,
 1941.7194032294385,
 1928.2119128971158,
 1900.0663996597482,
 1989.980205997232,
 1844.2213373379752,
 1951.9725944795941,
 1982.9977733647736,


In [8]:
import sklearn.metrics
import numpy as np

print('RMSE = ', np.sqrt(sklearn.metrics.mean_squared_error(dev0Expected, dev0Predicted)))
print('Model score = ', model.score(dev0X, dev0Expected))

/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/sklearn/metrics/_regression.py:95: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Please convert your data to numeric values explicitly instead.
  y_true = check_array(y_true, ensure_2d=False, dtype=dtype)


RMSE =  24.659364457329445
Model score =  0.8175627445862136


/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/sklearn/metrics/_regression.py:95: FutureWarning: Arrays of bytes/strings is being converted to decimal numbers if dtype='numeric'. This behavior is deprecated in 0.24 and will be removed in 1.1 (renaming of 0.26). Please convert your data to numeric values explicitly instead.
  y_true = check_array(y_true, ensure_2d=False, dtype=dtype)


In [24]:
predicted = [str(x) for x in dev0Predicted.tolist()]
writeOutput(predicted, 'dev-0/out.tsv')